# Maximum Clique using ILP

In [1]:
import numpy as np
import gurobipy as gb

## ILP for finding a maximum clique in an example graph

Consider the following graph $G=(V,E)$ with vertices $V=\{v_1,v_2,v_3,v_4\}$ and edges $E=\{(v_1,v_2),(v_1,v_3),(v_1,v_4),(v_3,v_4)\}$. Vertices $C=\{v_1,v_3,v_4\}$ form a clique, i.e. fully connected subgraph, of three vertices. This is a maximum clique, i.e. graph $G$ does not contain any other clique that is strictly larger.

Note that a clique corresponds to an independent set in the complement graph $\bar{G} = (V, \bar{E})$ where $\bar{E}$ consists of all nonedges of $G$. That is, $\bar{E} = \{(v_2,v_3),(v_2,v_4)\}$. Clearly, $C=\{v_1,v_3,v_4\}$ forms an independent set in $\bar{G}$, i.e. there exists no edge in $\bar{E}$ connecting two vertices in $C$.

We can use this property to write down the following integer linear program (ILP) for finding a maximum clique in $G$.

$$
\begin{align}
\max \quad & x_1 + x_2 + x_3 + x_4\\
\mathrm{s.t.}\quad & x_2 + x_3 \le 1\\
& x_2 + x_4 \le 1\\
& x_1,x_2,x_3,x_4 \in \{0,1\}
\end{align}
$$

where variables $x_1,x_2,x_3,x_4 \in \{0,1\}$ indicate the inclusion of the corresponding nodes $\{v_1,v_2,v_3,v_4\}$ in the clique $C$.

To implement this ILP, we start by initializing a model as follows.

In [2]:
m = gb.Model("clique")

Set parameter Username
Academic license - for non-commercial use only - expires 2025-04-01


Next, we add the variables $x_1,x_2,x_3,x_4 \in \{0,1\}$, indicating their domain using `vtype=gb.GRB.BINARY`.

In [3]:
x1 = m.addVar(vtype=gb.GRB.BINARY, name="v_1")
x2 = m.addVar(vtype=gb.GRB.BINARY, name="v_2")
x3 = m.addVar(vtype=gb.GRB.BINARY, name="v_3")
x4 = m.addVar(vtype=gb.GRB.BINARY, name="v_4")

We add the two constraints $x_2 + x_3 \le 1$ and $x_2 + x_4 \le 1$ as follows.

In [4]:
m.addConstr(x2+x3 <= 1)
m.addConstr(x2+x4 <= 1)

<gurobi.Constr *Awaiting Model Update*>

Finally, we add the objective function $\max x_1 + x_2 + x_3 + x_4$, indicating the optimization direction with `gb.GRB.MAXIMIZE`.

In [5]:
m.setObjective(x1 + x2 + x3 + x4, gb.GRB.MAXIMIZE)

We solve the ILP as follows.

In [6]:
m.optimize()

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 2 rows, 4 columns and 4 nonzeros
Model fingerprint: 0x7db9e7d6
Variable types: 0 continuous, 4 integer (4 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 2.0000000
Presolve removed 2 rows and 4 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.02 seconds (0.00 work units)
Thread count was 1 (of 10 available processors)

Solution count 2: 3 2 

Optimal solution found (tolerance 1.00e-04)
Best objective 3.000000000000e+00, best bound 3.000000000000e+00, gap 0.0000%


Note that the output above indicates that a solution with objective value $3$ was found. We can print the solution as follows.

In [7]:
for v in m.getVars():
    print(v.varName, v.x)

v_1 1.0
v_2 0.0
v_3 1.0
v_4 1.0


## ILP for finding a maximum clique in any graph

We can generalize the above ILP to finding a maximum clique in any graph $G=(V,E)$ as follows.
$$
\begin{align}
\max \quad & \sum_{v \in V} x_v\\
\mathrm{s.t.}\quad & x_i + x_j \le 1 & \forall v_i,v_j \in V, v_i \ne v_j, (v_i,v_j) \not \in E\\
& x_v \in \{0,1\} & \forall v \in V
\end{align}
$$

where each variable $x_v \in \{0,1\}$ indicates the inclusion of the corresponding node $v\in V$ in the clique $C$.

In [8]:
def parse_DIMACS(filename, relax):
    edges = set()
    with open(filename) as f:
        for line in f:
            if line.startswith('p'):
                nrVertices = int(line.rstrip("\n").split()[-2])
            elif line.startswith('e'):
                u = int(line.rstrip("\n").split()[-2])-1
                v = int(line.rstrip("\n").split()[-1])-1
                edges |= set([(u,v)])
    m = gb.Model(filename)
    t = gb.GRB.CONTINUOUS if relax else gb.GRB.BINARY
    x = m.addVars(range(nrVertices), vtype=t)
    for idx in range(len(x)):
        x[idx].varName = "x_" + str(idx)
    m.update()
    for i in range(nrVertices):
        for j in range(i+1, nrVertices):
            if ((i,j) not in edges) and ((j,i) not in edges):
                m.addConstr(x[i] + x[j] <= 1)
    if relax:
        for i in range(nrVertices):
            m.addConstr(x[i]<=1)
            m.addConstr(x[i]>=0)
    m.update()
    m.setObjective(gb.quicksum(x[i] for i in range(nrVertices)), gb.GRB.MAXIMIZE)
    m.update()
    return m, nrVertices

In the above code, the flag `relax` indicates whether to solve linear programming (LP) relaxation of the ILP. The argument `filename` points to a file in DIMACS format. We will solve the following graph `C125.9.clq.txt` with the following statistics.

In [9]:
!head -n 24 C125.9.clq.txt

c FILE:  C125.9.clq
c
c SOURCE: Generated by Michael Trick using
c         ggen, a program by Craig Morgenstern
c 
c DESCRIPTION: Cx.y is a random graph on x vertices
c              with edge probability .y
c
c 
c G(n,p) graph
c graph gen seed     : 74328432
c number of vertices : 125
c max number of edges: 20000
c edge probability   : 0.900000
c data structure     : dense
c
c           Graph Stats
c number of vertices  : 125
c nonisolated vertices: 125
c number of edges     : 6963
c edge density        : 0.898452
c max degree          : 119
c avg degree          : 111.41
c min degree          : 102


In [10]:
m, nrVertices = parse_DIMACS("./C125.9.clq.txt", False)

In [11]:
m.optimize()
for v in m.getVars():
    if v.x > 0:
        print(v.varName, v.x)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 787 rows, 125 columns and 1574 nonzeros
Model fingerprint: 0x8f991b58
Variable types: 0 continuous, 125 integer (125 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 26.0000000
Presolve removed 312 rows and 0 columns
Presolve time: 0.00s
Presolved: 475 rows, 125 columns, 1217 nonzeros
Variable types: 0 continuous, 125 integer (125 binary)

Root relaxation: objective 4.322903e+01, 362 iterations, 0.01 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0   43.22903    0  124   26.00000   43.22903  66.3%     - 

We can see that there is a maximum clique of size $34$. Dropping integrality, we get a different solution with objective value $62.5$.

In [12]:
m, nrVertices = parse_DIMACS("./C125.9.clq.txt", True)

In [13]:
m.optimize()
for v in m.getVars():
    if v.x > 0:
        print(v.varName, v.x)

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[rosetta2])

CPU model: Apple M1 Max
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 1037 rows, 125 columns and 1824 nonzeros
Model fingerprint: 0xbd83a7df
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 1e+00]
Presolve removed 250 rows and 0 columns
Presolve time: 0.01s
Presolved: 787 rows, 125 columns, 1574 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    6.6000000e+01   1.640000e+02   0.000000e+00      0s
      73    6.2500000e+01   0.000000e+00   0.000000e+00      0s

Solved in 73 iterations and 0.01 seconds (0.00 work units)
Optimal objective  6.250000000e+01
x_0 0.5
x_1 0.5
x_2 0.5
x_3 0.5
x_4 0.5
x_5 0.5
x_6 0.5
x_7 0.5
x_8 0.5
x_9 0.5
x_10 0.5
x_11 0.5
x_12 0.5
x_13 0.5
x_14 0.5
x_15 0.5
x_16 0.5
x_17 0.5
x_18 0.5
x_19 0.5
x_20 0.5